In [2]:
!pip install transformers[sentencepiece] datasets sacrebleu rouge_score py7zr -q

In [3]:

!nvidia-smi

Wed Feb  1 22:08:38 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 517.20       Driver Version: 517.20       CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ... WDDM  | 00000000:01:00.0 Off |                  N/A |
| N/A   54C    P8     6W /  N/A |      0MiB /  4096MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [4]:

!pip3 install keras --upgrade

In [5]:
from transformers import pipeline, set_seed

import matplotlib.pyplot as plt
from datasets import load_dataset
import pandas as pd
from datasets import load_dataset, load_metric
import numpy as np
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

import nltk
from nltk.tokenize import sent_tokenize

from tqdm import tqdm
import torch

nltk.download("punkt")

C:\Users\srija\anaconda3\envs\tf-gpu\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\srija\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [6]:
device="cuda" if torch.cuda.is_available() else "cpu"
device

'cuda'

In [7]:
model_ckpt = "google/pegasus-cnn_dailymail"

tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

model_pegasus = AutoModelForSeq2SeqLM.from_pretrained(model_ckpt).to(device)

In [8]:
import json

In [9]:
with open(r"C:\Users\srija\Py_torch1_stocks\train_set.json") as f:
     temp=json.load(f)

In [10]:
temp
data=temp['data']

In [11]:
data=temp['data']

In [12]:
data

[{'article': '\n\nDow Inc. (DOW) is a commodity chemical firm with a market cap of almost $47B. The company was spun out from conglomerate DowDuPont in April of 2019. Since its listing, Dow’s stock price has been volatile, ranging from a low close of $25.69 on March 9th, 2020 to a high close of $62.73 on March 1, 2021. Most of this volatility is, of course, due to economic uncertainty and disruption relating to COVID. The Q4 earnings (reported on January 28th, 2021) beat the consensus EPS expectation by almost 21% (EPS estimate = $0.67, actual EPS = $0.81). The share price has gained more than 12% since this earnings release. Part of this increase is probably related to the prediction that DOW will enjoy an earnings boost from higher polyethylene prices following the recent severe weather along the gulf coast. One feature of DOW that jumps out is the 4.5% dividend yield on a forward P/E of 17.16. The high yield is initially attractive, but it is worth noting that the payout ratio based

In [ ]:
dct1=({'article': 'Mountain Province Diamonds (TSE:MPVD) had its price objective dropped by stock analysts at Scotiabank from C$0.10 to C$0.05 in a research note issued to investors on Thursday, BayStreet.CA reports. Scotiabank’s price objective would suggest a potential downside of 88.89% from the company’s current price. Shares of traded down C$0.05 during trading on Thursday, hitting C$0.45. 359,396 shares of the company’s stock traded hands, compared to its average volume of 134,558. The firm’s fifty day moving average price is C$0.53 and its 200 day moving average price is C$0.57. Mountain Province Diamonds has a twelve month low of C$0.25 and a twelve month high of C$0.82. The company has a market cap of C$94.72 million and a PE ratio of -0.36. The company has a debt-to-equity ratio of 553.17, a current ratio of 1.70 and a quick ratio of 0.48. About Mountain Province Diamonds Mountain Province Diamonds Inc, through its subsidiaries, focuses on the mining and marketing of rough diamonds worldwide. Its primary asset is its 49% interest in the Gahcho KuÃ© diamond mine comprising of four mining leases covering an area of 10,353 hectares; and holds a 100% interest in the Kennady North project consisting of 22 federal leases and 97 claims covering an area of 106,202 hectares located in the Northwest Territories, Canada. .',
 'summary': 'Mountain Province Diamonds (TSE:MPVD) Given New C$0.05 Price Target at Scotiabank',
 'stock': 'BNS',
 'date': '2021-05-13'})



In [13]:
df= pd.DataFrame(columns=["Article","Summary"])
for i in range(0,len(data)):
    df.loc[i]=[data[i]["article"],data[i]["summary"]]

In [14]:
df

Article  \
0       \n\nDow Inc. (DOW) is a commodity chemical fir...   
1       Mountain Province Diamonds (TSE:MPVD) had its ...   
2       Blueshift Asset Management LLC bought a new po...   
3       VectivBio (NASDAQ:VECT)‘s stock had its “outpe...   
4       Virginia Retirement Systems ET AL reduced its ...   
...                                                   ...   
110529  Dimensional Fund Advisors LP trimmed its holdi...   
110530  Walled Lake Planning & Wealth Management LLC r...   
110531  Renaissance Group LLC grew its stake in shares...   
110532  NASDAQ END-OF-DAY STOCK REPORT\n\nGreen Plains...   
110533  SoFi Technologies (NASDAQ:SOFI – Get Rating) h...   

                                                  Summary  
0             Dow Has Little Upside, Significant Downside  
1       Mountain Province Diamonds (TSE:MPVD) Given Ne...  
2       Blueshift Asset Management LLC Acquires New St...  
3       Lifesci Capital Reaffirms “Outperform” Rating ...  
4       Virginia Retirement Systems ET AL Cuts Positio...  
...                                                   ...  
110529  Dimensional Fund Advisors LP Reduces Holdings ...  
110530  Pfizer Inc. (NYSE:PFE) is Walled Lake Planning...  
110531  Renaissance Group LLC Has $1.32 Million Stock ...  
110532  Green Plains Partners (GPP: $12.97) offers div...  
110533  SoFi Technologies (NASDAQ:SOFI) Price Target L...  

[110534 rows x 2 columns]

In [15]:
train_train,train_test =np.split(df.sample(frac=0.3),[int(0.25*len(df))])

In [18]:
train_train

Article  \
90882  12:10 EST Fed funds futures are now priced for...   
12565  As businesses are growing sales rapidly and ar...   
71258  Shell Asset Management Co. trimmed its stake i...   
95388  PennyMac Financial Services, Inc. (NYSE:PFSI –...   
77914  Beacon Pointe Advisors LLC decreased its stake...   
...                                                  ...   
62850  AUSTRALIAN END-OF-DAY STOCK REPORT\n\nWestpac ...   
77092  StockNews.com started coverage on shares of Ac...   
42418  Rockefeller Capital Management L.P. lessened i...   
77267  MILWAUKEE, February 15, 2022 BUSINESS WIRE Roc...   
5457   Medallion Financial (NASDAQ:MFIN) was upgraded...   

                                                 Summary  
90882  12:10 EST Fed funds futures are now priced for...  
12565  3 High-Growth Stocks That Are Just Getting Sta...  
71258  Shell Asset Management Co. Decreases Stock Hol...  
95388  Research Analysts Offer Predictions for PennyM...  
77914  Beacon Pointe Advisors LLC Sells 4,413 Shares ...  
...                                                  ...  
62850  Westpac Banking (WBC: $A20.85) offers 3rd high...  
77092  Acorda Therapeutics (NASDAQ:ACOR) Now Covered ...  
42418  Equitable Holdings, Inc. (NYSE:EQH) Stock Posi...  
77267  Rockwell Automation to Present at Citi’s 2022 ...  
5457   Zacks Investment Research Upgrades Medallion F...  

[27633 rows x 2 columns]

In [16]:
import pyarrow as pa
import pyarrow.dataset as ds

from datasets import Dataset


dataset = ds.dataset(pa.Table.from_pandas(train_train).to_batches())

### convert to Huggingface dataset
hg_dataset = Dataset(pa.Table.from_pandas(train_train))

In [17]:
import pyarrow as pa
import pyarrow.dataset as ds

from datasets import Dataset


dataset = ds.dataset(pa.Table.from_pandas(train_train).to_batches())

### convert to Huggingface dataset
hg_dataset_val = Dataset(pa.Table.from_pandas(train_test))

In [18]:
hg_dataset_val

Dataset({
    features: ['Article', 'Summary', '__index_level_0__'],
    num_rows: 5527
})

In [19]:
temp1=df.iloc[:,0]

In [20]:
temp1

0         \n\nDow Inc. (DOW) is a commodity chemical fir...
1         Mountain Province Diamonds (TSE:MPVD) had its ...
2         Blueshift Asset Management LLC bought a new po...
3         VectivBio (NASDAQ:VECT)‘s stock had its “outpe...
4         Virginia Retirement Systems ET AL reduced its ...
                                ...                        
110529    Dimensional Fund Advisors LP trimmed its holdi...
110530    Walled Lake Planning & Wealth Management LLC r...
110531    Renaissance Group LLC grew its stake in shares...
110532    NASDAQ END-OF-DAY STOCK REPORT\n\nGreen Plains...
110533    SoFi Technologies (NASDAQ:SOFI – Get Rating) h...
Name: Article, Length: 110534, dtype: object

In [21]:
temp2=df.iloc[:,1]

In [22]:
temp2[2]

'Blueshift Asset Management LLC Acquires New Stake in Baidu, Inc. (NASDAQ:BIDU)'

In [23]:
max1=0
max1
max_index=0

In [24]:
for i in range(0,len(temp1)):
    pemp=len(temp1[i])
    if pemp>max1:
        max1=pemp
        max_index=i
                    
            
            
max1
temp1[max_index]

'NYSE END-OF-DAY STOCK REPORT\n\nDominion Energy, Inc. (NYSE:D), the NYSE\'s 3rd largest Conventional electricity company by market cap, has increased $1.23 (1.5%) from its previous trading session to close at $80.72. Compared with the S&P 500 Index which fell 23.1 points (0.5%) in the day, the relative price increase was 2.1%. \n\nThere were 3,505,044 shares worth $282.9 million traded today. The volume was close to average trading.\n\nFinancial News\nAnnual Report (FY 2021):\nRelease Date: February 26, 2022\nFY2021 Annual Report: Dominion Energy Revenue down 1.5%\nDominion Energy (NYSE:D) reported total revenue for the year-ended 31 December 2021 [FY2021] of $14.0b, down 1.5% from $14.2b in the previous year [FY2020]. \nMajor changes compared with previous year (FY2021 vs FY2020):\nFavourable Changes:\nEBIT Margin up from 19.7% to 31.9%\nInterest cover up 62.9% from 2.0 to 3.3\nEBIT to total assets up from 2.9% to 4.5%\nProfit before tax to Revenues up from 10% to 22.2%\nCurrent rati

In [25]:
min1=200000
min_index=0

for i in range(0,len(temp1)):
    pemp=len(temp1[i])
    if pemp<min1:
        min1=pemp
        min_index=i
        
min1
#temp1[min_index]

301

In [26]:
max2=0
for i in range(0,len(temp2)):
    pemp=len(temp2[i])
    if pemp>max2:
        max2=pemp
        #max_index=i
max2

255

In [27]:
min2=256
for i in range(0,len(temp2)):
    pemp=len(temp2[i])
    if pemp<min2:
        min2=pemp
min2

9

In [ ]:
##summarization

pipe = pipeline('summarization', model = model_ckpt )



In [28]:
 def generate_batch_sized_chunks(list_of_elements, batch_size):
     """split the dataset into smaller batches that we can process simultaneously
     Yield successive batch-sized chunks from list_of_elements."""
     for i in range(0, len(list_of_elements), batch_size):
        yield list_of_elements[i : i + batch_size]


In [29]:
def calculate_metric_on_test_ds(dataset, metric, model, tokenizer, 
                               batch_size=1, device=device, 
                               column_text="article", 
                               column_summary="highlights"):
    article_batches = list(generate_batch_sized_chunks(dataset[column_text], batch_size))
    target_batches = list(generate_batch_sized_chunks(dataset[column_summary], batch_size))

    for article_batch, target_batch in tqdm(
        zip(article_batches, target_batches), total=len(article_batches)):
        
        inputs = tokenizer(article_batch, max_length=50000,  truncation=True, 
                        padding="max_length", return_tensors="pt")
        
        summaries = model.generate(input_ids=inputs["input_ids"].to(device),
                         attention_mask=inputs["attention_mask"].to(device), 
                         length_penalty=0.8, num_beams=8, max_length=256)
        ''' parameter for length penalty ensures that the model does not generate sequences that are too long. '''
        
        # Finally, we decode the generated texts, 
        # replace the  token, and add the decoded texts with the references to the metric.
        decoded_summaries = [tokenizer.decode(s, skip_special_tokens=True, 
                                clean_up_tokenization_spaces=True) 
               for s in summaries]      
        
        decoded_summaries = [d.replace("", " ") for d in decoded_summaries]
        
        
        metric.add_batch(predictions=decoded_summaries, references=target_batch)
        
    #  Finally compute and return the ROUGE scores.
    score = metric.compute()
    return score

In [30]:
!pip install GPUtil
!pip install numba
import torch
from GPUtil import showUtilization as gpu_usage
from numba import cuda

def free_gpu_cache():
    print("Initial GPU Usage")
    gpu_usage()                             

    torch.cuda.empty_cache()

    cuda.select_device(0)
    cuda.close()
    cuda.select_device(0)

    print("GPU Usage after emptying the cache")
    gpu_usage()

free_gpu_cache()  

Initial GPU Usage
| ID | GPU | MEM |
------------------
|  0 |  0% | 55% |
GPU Usage after emptying the cache
| ID | GPU | MEM |
------------------
|  0 |  2% |  2% |


In [32]:



from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

device = "cuda" if torch.cuda.is_available() else "cpu"

model_ckpt = "google/pegasus-cnn_dailymail"

tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

model_pegasus = AutoModelForSeq2SeqLM.from_pretrained(model_ckpt).to(device)

RuntimeError: CUDA error: invalid argument
CUDA kernel errors might be asynchronously reported at some other API call,so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.

In [33]:
rouge_metric = load_metric('rouge')

score = calculate_metric_on_test_ds(hg_dataset, rouge_metric, model_pegasus, tokenizer, column_text = 'Article', column_summary='Summary', batch_size=16)

C:\Users\srija\AppData\Local\Temp\ipykernel_21796\1004742056.py:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  rouge_metric = load_metric('rouge')
  0%|          | 0/1728 [00:00<?, ?it/s]


RuntimeError: CUDA error: invalid argument
CUDA kernel errors might be asynchronously reported at some other API call,so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.

In [34]:
!nvidia-smi

Wed Feb  1 22:30:37 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 517.20       Driver Version: 517.20       CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ... WDDM  | 00000000:01:00.0 Off |                  N/A |
| N/A   50C    P8     6W /  N/A |    816MiB /  4096MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
# from transformers import PegasusForConditionalGeneration, PegasusTokenizer
# # Load tokenizer 
# tokenizer = PegasusTokenizer.from_pretrained("google/pegasus-cnn_dailymail")
# # Load model 
# model = PegasusForConditionalGeneration.from_pretrained("google/pegasus-cnn_dailymail")

In [ ]:
# tokens = tokenizer(a, truncation=True, padding="longest", return_tensors="pt")
# # Input tokens
# summary = model.generate(**tokens)

# tokenizer.decode(summary[0])

In [35]:
def convert_examples_to_features(example_batch):
    input_encodings = tokenizer(example_batch['Article'] , max_length = 205000, truncation = True )
    
    with tokenizer.as_target_tokenizer():
        target_encodings = tokenizer(example_batch['Summary'], max_length = 256, truncation = True )
        
    return {
        'input_ids' : input_encodings['input_ids'],
        'attention_mask': input_encodings['attention_mask'],
        'labels': target_encodings['input_ids']
    }
    
dataset_df_pt = hg_dataset.map(convert_examples_to_features, batched = True)


  0%|          | 0/28 [00:00<?, ?ba/s]C:\Users\srija\anaconda3\envs\tf-gpu\lib\site-packages\transformers\tokenization_utils_base.py:3581: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(
100%|██████████| 28/28 [00:26<00:00,  1.06ba/s]


In [36]:
dataset_df_pt_train =  hg_dataset_val.map(convert_examples_to_features, batched = True)


100%|██████████| 6/6 [00:05<00:00,  1.13ba/s]


In [37]:
dataset_df_pt_train

Dataset({
    features: ['Article', 'Summary', '__index_level_0__', 'input_ids', 'attention_mask', 'labels'],
    num_rows: 5527
})

In [38]:

from transformers import DataCollatorForSeq2Seq

seq2seq_data_collator = DataCollatorForSeq2Seq(tokenizer, model=model_pegasus)

In [39]:
from transformers import TrainingArguments, Trainer

trainer_args = TrainingArguments(
    output_dir='news_byte', num_train_epochs=1, warmup_steps=500,
    per_device_train_batch_size=1, per_device_eval_batch_size=1,
    weight_decay=0.01, logging_steps=10,
    evaluation_strategy='steps', eval_steps=500, save_steps=1e6,
    gradient_accumulation_steps=16
) 





In [40]:
trainer = Trainer(model=model_pegasus, args=trainer_args,
                  tokenizer=tokenizer, data_collator=seq2seq_data_collator,
                  train_dataset=dataset_df_pt, 
                  eval_dataset=dataset_df_pt_train )
     

In [41]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `PegasusForConditionalGeneration.forward` and have been ignored: Summary, __index_level_0__, Article. If Summary, __index_level_0__, Article are not expected by `PegasusForConditionalGeneration.forward`,  you can safely ignore this message.
C:\Users\srija\anaconda3\envs\tf-gpu\lib\site-packages\transformers\optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 27633
  Num Epochs = 1
  Instantaneous batch size per device = 1
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 16
  Total optimization steps = 1727
  Number of trainable parameters = 568699904


RuntimeError: CUDA error: invalid argument
CUDA kernel errors might be asynchronously reported at some other API call,so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.

In [42]:
torch.cuda.current_device()

0

In [43]:
torch.cuda.memory_allocated()

2284199424

In [44]:
torch.cuda.get_device_name()

'NVIDIA GeForce RTX 3050 Laptop GPU'

In [45]:
torch.cuda.memory_cached()

C:\Users\srija\anaconda3\envs\tf-gpu\lib\site-packages\torch\cuda\memory.py:391: FutureWarning: torch.cuda.memory_cached has been renamed to torch.cuda.memory_reserved
  warnings.warn(


3082813440

In [46]:
!nvidia-smi

Wed Feb  1 22:32:16 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 517.20       Driver Version: 517.20       CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ... WDDM  | 00000000:01:00.0 Off |                  N/A |
| N/A   52C    P8     6W /  N/A |    818MiB /  4096MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [47]:
score = calculate_metric_on_test_ds(hg_dataset
    , rouge_metric, trainer.model, tokenizer, batch_size = 2, column_text = 'Article', column_summary= 'Summary'
)

rouge_dict = dict((rn, score[rn].mid.fmeasure ) for rn in rouge_names )

pd.DataFrame(rouge_dict, index = [f'pegasus'] )

  0%|          | 0/13817 [00:00<?, ?it/s]


RuntimeError: CUDA error: invalid argument
CUDA kernel errors might be asynchronously reported at some other API call,so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.

In [48]:
model_pegasus.save_pretrained("pegasus-stock-model")

Configuration saved in pegasus-stock-model\config.json
Configuration saved in pegasus-stock-model\generation_config.json


RuntimeError: CUDA error: invalid argument
CUDA kernel errors might be asynchronously reported at some other API call,so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.

In [49]:
tokenizer.save_pretrained("tokenizer")

tokenizer config file saved in tokenizer\tokenizer_config.json
Special tokens file saved in tokenizer\special_tokens_map.json


('tokenizer\\tokenizer_config.json',
 'tokenizer\\special_tokens_map.json',
 'tokenizer\\spiece.model',
 'tokenizer\\added_tokens.json',
 'tokenizer\\tokenizer.json')